<a href="https://colab.research.google.com/github/CakeNuthep/Create_Knowledge_Graph/blob/main/DBLP_XML_Dask.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#ทำการ mount Google Drive ที่เก็บข้อมูล DBLP-XML
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd

In [ ]:
!python -m pip install dask[dataframe] --upgrade

     |████████████████████████████████| 942kB 13.1MB/s 
     |████████████████████████████████| 112kB 46.5MB/s 
  Found existing installation: dask 2.12.0
    Uninstalling dask-2.12.0:
      Successfully uninstalled dask-2.12.0


In [ ]:
!pip install memory_profiler

  Created wheel for memory-profiler: filename=memory_profiler-0.58.0-cp37-none-any.whl size=30180 sha256=a49b890f62f5499816f7cd1a5fb17775d7f64e449c0beb91b989c01b2286cbdd
  Stored in directory: /root/.cache/pip/wheels/02/e4/0b/aaab481fc5dd2a4ea59e78bc7231bb6aae7635ca7ee79f8ae5
Successfully built memory-profiler


In [ ]:
import dask
import dask.dataframe as dd

# Convert String to JSON

## Checkpoint 1

In [ ]:
path_file = '/content/drive/MyDrive/KnowledgeGraph/Json_researcher/dblp-xml.json'

In [ ]:
# เนื่องจากข้อมูล dbkp-xml.json ยังไม่ใช่รูปแบบ json ทีสมบูรณ์จึงต้องปรับแก้ข้อมูลเพื่อให้เป็นรูปแบบ json ที่สมบูรณ์
# ตัวอย่างข้อมูลที่มีเป็นประมาณดังนี้
# 
# {data}
# {data}
# {data}
#
# ทำการอ่านไฟล์ dbkp-xml.json เพื่อทำการเพิ่ม "[" ที่ด้านหน้าสุดของไฟล์ และเพิ่ม "]" ที่ท้ายสุดของไฟล์ และแต่ละบรรทัดจะต้องคั่นด้วย ","
# ผลลัพธ์หลังจากปรับแก้ควรเป็น
#
#[
# {data},
# {data},
# {data}  
#]
# 

f = open(path_file, "r",encoding="utf8")
count = 0
content = []
string_json = ''
begin = '['
end = ']'
split = ','

string_json += begin
while(True):
    # Read a line.
    line = f.readline()
    # When readline returns an empty string, the file is fully read.
    if line == "":
        print("::DONE::")
        break
    if count != 0:
      string_json += split
    string_json += line
    content.append(line)
    count +=1

string_json += end

::DONE::


In [ ]:
# ทำการแปลงข้อมูล json เป็น Dictionay ใน Python

import json
data = json.loads(string_json)

NameError: ignored

In [ ]:
data[0:1000]

[{'_id': 'journals/cin/WangW17',
  '_index': 'dblp-xml',
  '_score': 1,
  '_source': {'author': ['Zheng Wang 0032', 'Qingbiao Wu'],
   'ee': ['https://doi.org/10.1155/2017/5705693',
    'https://www.wikidata.org/entity/Q41214384'],
   'elt': 'article',
   'file': '/Users/polnoy/Documents/app/tnrr-puller/assets/dblp/dblp-2020-03-01.xml',
   'journal': 'Comp. Int. and Neurosc.',
   'key': 'journals/cin/WangW17',
   'mdate': '2018-11-14',
   'no': 2197004,
   'pages': '5705693:1-5705693:10',
   'pullDate': '2020-04-09T04:41:04.378Z',
   'title': 'Shape Completion Using Deep Boltzmann Machine.',
   'url': 'db/journals/cin/cin2017.html#WangW17',
   'volume': '2017',
   'year': '2017'},
  '_type': 'dblp-xml'},
 {'_id': 'journals/cin/DevlaminckWGOS11',
  '_index': 'dblp-xml',
  '_score': 1,
  '_source': {'author': ['Dieter Devlaminck',
    'Bart Wyns',
    'Moritz Grosse-Wentrup',
    'Georges Otte',
    'Patrick Santens'],
   'ee': ['https://doi.org/10.1155/2011/217987',
    'https://www.wik

In [ ]:
# ทำการแปลง Dictionary เป็น Dataframe
df = pd.json_normalize(data)

In [ ]:
df

_index     _type  ... _source.address  _source.chapter
0        dblp-xml  dblp-xml  ...             NaN              NaN
1        dblp-xml  dblp-xml  ...             NaN              NaN
2        dblp-xml  dblp-xml  ...             NaN              NaN
3        dblp-xml  dblp-xml  ...             NaN              NaN
4        dblp-xml  dblp-xml  ...             NaN              NaN
...           ...       ...  ...             ...              ...
2205795  dblp-xml  dblp-xml  ...             NaN              NaN
2205796  dblp-xml  dblp-xml  ...             NaN              NaN
2205797  dblp-xml  dblp-xml  ...             NaN              NaN
2205798  dblp-xml  dblp-xml  ...             NaN              NaN
2205799  dblp-xml  dblp-xml  ...             NaN              NaN

[2205800 rows x 36 columns]

In [ ]:
# ทำการ Export เป็น csv file
df.to_csv('/content/dblp_xml_raw.csv')

In [ ]:
# !cp /content/drive/MyDrive/KnowledgeGraph/dblp_xml_raw.csv /content/dblp_xml_raw.csv

## Checkpoint2

In [ ]:
# ทำการอ่านไฟล์ csv

header = [ 'index'        		
  '_index'             
  '_type'              
  '_id'                
  '_score'             
  '_source.elt'        
  '_source.mdate'      
  '_source.key'        
  '_source.author'     
  '_source.ee'         
  '_source.title'      
  '_source.pages'      
  '_source.year'       
  '_source.volume'     
  '_source.journal'    
  '_source.url'        
  '_source.file'       
  '_source.no'         
  '_source.pullDate'   
  '_source.number'     
  '_source.i'          
  '_source.sup'        
  '_source.sub'        
  '_source.note'       
  '_source.editor'     
  '_source.isbn'       
  '_source.booktitle'  
  '_source.series'     
  '_source.publisher'  
  '_source.crossref'   
  '_source.cite'       
  '_source.cdrom'      
  '_source.school'     
  '_source.month'      
  '_source.tt'         
  '_source.address'    
  '_source.chapter'    
  'new_name'           
  ]
types = {'Unnamed: 0'          		 :'int64',  
  '_index'             :'object', 
  '_type'              :'object', 
  '_id'                :'object', 
  '_score'             :'int64',  
  '_source.elt'        :'object', 
  '_source.mdate'      :'object', 
  '_source.key'        :'object', 
  '_source.author'     :'object', 
  '_source.ee'         :'object', 
  '_source.title'      :'object', 
  '_source.pages'      :'object', 
  '_source.year'       :'int64', 
  '_source.volume'     :'object', 
  '_source.journal'    :'object', 
  '_source.url'        :'object', 
  '_source.file'       :'object', 
  '_source.no'         :'int64',  
  '_source.pullDate'   :'object', 
  '_source.number'     :'object',
  '_source.i'          :'object', 
  '_source.sup'        :'object', 
  '_source.sub'        :'object', 
  '_source.note'       :'object', 
  '_source.editor'     :'object', 
  '_source.isbn'       :'object', 
  '_source.booktitle'  :'object', 
  '_source.series'     :'object', 
  '_source.publisher'  :'object', 
  '_source.crossref'   :'object', 
  '_source.cite'       :'object', 
  '_source.cdrom'      :'object', 
  '_source.school'     :'object', 
  '_source.month'      :'object', 
  '_source.tt'         :'object', 
  '_source.address'    :'object', 
  '_source.chapter'    :'float64',
  'new_name'           :'object' }

# df = dd.read_csv('/content/drive/MyDrive/KnowledgeGraph/dblp_xml_raw.csv', names=header, dtype=types, header=0).set_index('index')
df = dd.read_csv('/content/dblp_xml_raw.csv', dtype=types, header=0).set_index('Unnamed: 0')

In [ ]:
df

Dask DataFrame Structure:
                _index   _type     _id _score _source.elt _source.mdate _source.key _source.author _source.ee _source.title _source.pages _source.year _source.volume _source.journal _source.url _source.file _source.no _source.pullDate _source.number _source.i _source.sup _source.sub _source.note _source.editor _source.isbn _source.booktitle _source.series _source.publisher _source.crossref _source.cite _source.cdrom _source.school _source.month _source.tt _source.address _source.chapter
npartitions=17                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
0               object  object  object  int64      object        object      object         object     object        object        object        int64         object          object      object       object      int64           object         object    object      object      object       object         object       object            object         object            object           object       object        object         object        object     object          object         float64
129852             ...     ...     ...    ...         ...           ...         ...            ...        ...           ...           ...          ...            ...             ...         ...          ...        ...              ...            ...       ...         ...         ...          ...            ...          ...               ...            ...               ...              ...          ...           ...            ...           ...        ...             ...             ...
...                ...     ...     ...    ...         ...           ...         ...            ...        ...           ...           ...          ...            ...             ...         ...          ...        ...              ...            ...       ...         ...         ...          ...            ...          ...               ...            ...               ...              ...          ...           ...            ...           ...        ...             ...             ...
2083322            ...     ...     ...    ...         ...           ...         ...            ...        ...           ...           ...          ...            ...             ...         ...          ...        ...              ...            ...       ...         ...         ...          ...            ...          ...               ...            ...               ...              ...          ...           ...            ...           ...        ...             ...             ...
2205799            ...     ...     ...    ...         ...           ...         ...            ...        ...           ...           ...          ...            ...             ...         ...          ...        ...              ...            ...       ...         ...         ...          ...            ...          ...               ...            ...               ...              ...          ...           ...            ...           ...        ...             ...             ...
Dask Name: sort_index, 51 tasks

In [ ]:
df.head()

_index     _type  ... _source.address  _source.chapter
Unnamed: 0                      ...                                 
0           dblp-xml  dblp-xml  ...             NaN              NaN
1           dblp-xml  dblp-xml  ...             NaN              NaN
2           dblp-xml  dblp-xml  ...             NaN              NaN
3           dblp-xml  dblp-xml  ...             NaN              NaN
4           dblp-xml  dblp-xml  ...             NaN              NaN

[5 rows x 36 columns]

In [ ]:
df = df.assign(new_name=df['_source.author'].str.split(","))
df['new_name'] = df['_source.author']

In [ ]:
#เนื่องจากข้อมูล _source.author สามารถเก็บชื่อได้หลายชื่อที่คั่นด้วย "," เราจึงต้องทำการ Split ชื่อออกมาเป็น array มาใส่ในคอลัมน์ที่ชื่อว่า new_name
df['new_name'] = df.new_name.apply(lambda x: x[1:-1].split(','))

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:3519: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('new_name', 'object'))

  warnings.warn(meta_warning(meta))


# separate dblp

In [ ]:
import pandas as pd

def is_english(str):
    for i in str:
        if i in ('A','B','C','D','E','F','G','H','I','J','K','L','M','N','O','P','Q','R','S','T','U','V','W','X','Y','Z','a','b','c','d','e','f','g','h','i','j','k','l','m','n','o','p','q','r','s','t','u','v','w','x','y','z'):
            return True
    else:    
        return False

def is_thai(str):
    for i in str:
        if i in ('ก','ข','ฃ','ค','ฅ','ฆ','ง','จ','ฉ','ช','ซ','ฌ','ญ','ฎ','ฏ','ฐ','ฑ','ฒ','ณ','ด','ต','ถ','ท','ธ','น','บ','ป','ผ','ฝ','พ','ฟ','ภ','ม','ย','ร','ล','ว','ศ','ษ','ส','ห','ฬ','อ','ฮ'):
            return True
    else:
        return False

def language(text):
    if is_english(text):
      return 'eng'
    elif is_thai(text):
      return 'th'
    else:
      return 'other'

def strip_row(text):
    text = text.strip()
    text = ' '.join(text.split())
    return text

def first_name(list_text):
    name = ''
    if len(list_text) > 0:
      name = strip_row(list_text[0])
    return name

def check_first_author(row):
    if pd.isna(row['first_name']):
      return 'no'
    elif pd.isna(row['new_name']):
      return 'no'
    elif row['first_name'] == '':
      return 'no'
    elif row['first_name'] == row['new_name']:
      return 'yes'
    else:
      return 'no'

In [ ]:
df.head()

_index  ...                                           new_name
Unnamed: 0            ...                                                   
0           dblp-xml  ...                ['Zheng Wang 0032',  'Qingbiao Wu']
1           dblp-xml  ...  ['Dieter Devlaminck',  'Bart Wyns',  'Moritz G...
2           dblp-xml  ...  ['Julius Gelsvartas',  'Rimvydas Simutis',  'R...
3           dblp-xml  ...  ['Ioannis Xygonakis',  'Alkinoos Athanasiou', ...
4           dblp-xml  ...       ['Haorui Liu',  'Feng-Yan Yi',  'Heli Yang']

[5 rows x 37 columns]

In [ ]:
df_new_author = df

In [ ]:
df_new_author.head()

_index  ...                                           new_name
Unnamed: 0            ...                                                   
0           dblp-xml  ...                ['Zheng Wang 0032',  'Qingbiao Wu']
1           dblp-xml  ...  ['Dieter Devlaminck',  'Bart Wyns',  'Moritz G...
2           dblp-xml  ...  ['Julius Gelsvartas',  'Rimvydas Simutis',  'R...
3           dblp-xml  ...  ['Ioannis Xygonakis',  'Alkinoos Athanasiou', ...
4           dblp-xml  ...       ['Haorui Liu',  'Feng-Yan Yi',  'Heli Yang']

[5 rows x 37 columns]

In [ ]:
#สร้าง column ที่ชื่อว่า first_name สำหรับเก็บว่าชื่อแรกใน paper ชื่อว่าอะไร
df_new_author['first_name'] = df_new_author['new_name'].apply(first_name)

#หลังจากทำการ Split ชื่อออกมาเป็น array มาใส่ในคอลัมน์ที่ชื่อว่า new_name เสร็จแล้วให้ทำการ Duplicate Row โดยเอาชื่อที่ถูก Splite ไปใส่ใน Row ใหม่ และชื่อที่ถูก Splite มาใส่ในคอลัมน์ที่ชื่อว่า new_name
df_new_author = df_new_author.explode('new_name')

#ทำการ Duplicate Row โดยการ Splite ชื่อในคอลัม new_name ที่คั่นด้วย ; แล้วเอาชื่อที่ถูก Splite ไปใส่ใน Row ใหม่ และชื่อที่ถูก Splite มาใส่ในคอลัมน์ใหม่ที่ชื่อว่า new_name
df_new_author = df_new_author.assign(new_name=df_new_author['new_name'].str.split(";"))
df_new_author = df_new_author.explode('new_name')

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:3519: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('new_name', 'object'))

  warnings.warn(meta_warning(meta))


In [ ]:
df_new_author.head()

_index     _type  ...                  new_name           first_name
Unnamed: 0                      ...                                               
0           dblp-xml  dblp-xml  ...         'Zheng Wang 0032'    'Zheng Wang 0032'
0           dblp-xml  dblp-xml  ...             'Qingbiao Wu'    'Zheng Wang 0032'
1           dblp-xml  dblp-xml  ...       'Dieter Devlaminck'  'Dieter Devlaminck'
1           dblp-xml  dblp-xml  ...               'Bart Wyns'  'Dieter Devlaminck'
1           dblp-xml  dblp-xml  ...   'Moritz Grosse-Wentrup'  'Dieter Devlaminck'

[5 rows x 38 columns]

In [ ]:
df_new = df_new_author

In [ ]:
df_new.head()

_index     _type  ...                  new_name           first_name
Unnamed: 0                      ...                                               
0           dblp-xml  dblp-xml  ...         'Zheng Wang 0032'    'Zheng Wang 0032'
0           dblp-xml  dblp-xml  ...             'Qingbiao Wu'    'Zheng Wang 0032'
1           dblp-xml  dblp-xml  ...       'Dieter Devlaminck'  'Dieter Devlaminck'
1           dblp-xml  dblp-xml  ...               'Bart Wyns'  'Dieter Devlaminck'
1           dblp-xml  dblp-xml  ...   'Moritz Grosse-Wentrup'  'Dieter Devlaminck'

[5 rows x 38 columns]

In [ ]:
#ทำการกำจัด White space เป็น space เดียวในคอลัมน์ที่ชื่อว่า new_name และ first_name
df_new['new_name'] = df_new['new_name'].apply(strip_row)
df_new['first_name'] = df_new['first_name'].apply(strip_row)

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:3519: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('new_name', 'object'))

  warnings.warn(meta_warning(meta))
/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:3519: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('first_name', 'object'))

  warnings.war

In [ ]:
df_new.head()

_index     _type  ...                 new_name           first_name
Unnamed: 0                      ...                                              
0           dblp-xml  dblp-xml  ...        'Zheng Wang 0032'    'Zheng Wang 0032'
0           dblp-xml  dblp-xml  ...            'Qingbiao Wu'    'Zheng Wang 0032'
1           dblp-xml  dblp-xml  ...      'Dieter Devlaminck'  'Dieter Devlaminck'
1           dblp-xml  dblp-xml  ...              'Bart Wyns'  'Dieter Devlaminck'
1           dblp-xml  dblp-xml  ...  'Moritz Grosse-Wentrup'  'Dieter Devlaminck'

[5 rows x 38 columns]

In [ ]:
# ทำการตรวจสอบว่า Row ใหนเป็นชื่อแรกที่มาจากคอลัมน์ author แล้วกำหนดค่าใหม่ใน Column ที่ชื่อว่า first_author โดยจะมีค่าดังนี้
#   yes หากเป็นชื่อแรก
#   no  หากไม่ใช่ชื่อแรก
df_new['first_author'] = df_new.apply(check_first_author,axis=1) 

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:4681: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=(None, 'object'))

  warnings.warn(meta_warning(meta))


In [ ]:
df_new.head()

_index     _type  ...           first_name  first_author
Unnamed: 0                      ...                                   
0           dblp-xml  dblp-xml  ...    'Zheng Wang 0032'           yes
0           dblp-xml  dblp-xml  ...    'Zheng Wang 0032'            no
1           dblp-xml  dblp-xml  ...  'Dieter Devlaminck'           yes
1           dblp-xml  dblp-xml  ...  'Dieter Devlaminck'            no
1           dblp-xml  dblp-xml  ...  'Dieter Devlaminck'            no

[5 rows x 39 columns]

# clean name

In [ ]:
def front(name, title):
    if name.find(title)>-1 and name.startswith(title):
        a = []
        b = ''
        for i in name:
            a.append(i)
        for i in range(len(title)):
            del a[0]
        for i in a:
            b = b+i
    return b 

def behind(name, title):
    if name.find(title)>-1 and name.endswith(title):
        a = []
        b = ''
        for i in name:
            a.append(i)
        for i in range(name.rfind(title),len(name)):
            del a[name.rfind(title)]
        for i in a:
            b = b+i
    return b

In [ ]:
def deltitlefull(str):
    a = str
    b = []
    b.append(a)
    prefix = ''
    for i in b:
        if i in ('ว่าที่','จอมพล','พลเอก','พลโท','พลตรี','พลจัตวา','พันเอก','พันโท','พันตรี','ร้อยเอก','ร้อยโท','ร้อยตรี','จ่าสิบเอกพิเศษ','จ่าสิบเอก','จ่าสิบโท','จ่าสิบตรี','สิบเอก','สิบโท','สิบตรี','จอมพลเรือ','พลเรือเอก','พลเรือโท','พลเรือตรี','พลเรือจัตวา','นาวาเอก','นาวาโท','นาวาตรี','เรือเอก','เรือโท','เรือตรี','พันจ่าเอก','พันจ่าโท','พันจ่าตรี','จ่าเอก','จ่าโท','จ่าตรี','จอมพลอากาศ','พลอากาศเอก','พลอากาศโท','พลอากาศตรี','พลอากาศจัตวา','นาวาอากาศเอก','นาวาอากาศโท','นาวาอากาศตรี','เรืออากาศเอก','เรืออากาศโท','เรืออากาศตรี','พันจ่าอากาศเอก','พันจ่าอากาศโท','พันจ่าอากาศตรี','จ่าอากาศเอก','จ่าอากาศโท','จ่าอากาศตรี','พลตำรวจเอก','พลตำรวจโท','พลตำรวจตรี','พลตำรวจจัตวา','พันตำรวจเอก','พันตำรวจโท','พันตำรวจตรี','ร้อยตำรวจเอก','ร้อยตำรวจโท','ร้อยตำรวจตรี','ดาบตำรวจ','จ่าสิบตำรวจ','สิบตำรวจเอก','สิบตำรวจโท','สิบตำรวจตรี','หม่อมหลวง','ผู้ช่วยศาสตราจารย์','รองศาสตราจารย์','ศาสตราจารย์','อาจารย์','แพทย์หญิง','นายแพทย์','นาง','นางสาว','นาย'):
            return a, prefix
    c = ['ฯพณฯ']
    c1 = ['ผู้ช่วยศาสตราจารย์พิเศษ','รองศาสตราจารย์พิเศษ','ศาสตราจารย์พิเศษ','อาจารย์พิเศษ','ผู้ช่วยศาสตราจารย์','รองศาสตราจารย์','ศาสตราจารย์กิตติคุณ','ศาสตราจารย์เกียรติยศ','ศาสตราจารย์','อาจารย์']
    c2 = ['ว่าที่']
    c3 = ['จอมพลพิเศษหญิง','พลเอกพิเศษหญิง','พลโทพิเศษหญิง','พลตรีพิเศษหญิง','พลจัตวาพิเศษหญิง','พันเอกพิเศษหญิง','พันโทพิเศษหญิง','พันตรีพิเศษหญิง','ร้อยเอกพิเศษหญิง','ร้อยโทพิเศษหญิง','ร้อยตรีพิเศษหญิง','จ่าสิบเอกพิเศษพิเศษหญิง','จ่าสิบเอกพิเศษหญิง','จ่าสิบโทพิเศษหญิง','จ่าสิบตรีพิเศษหญิง','สิบเอกพิเศษหญิง','สิบโทพิเศษหญิง','สิบตรีพิเศษหญิง','จอมพลเรือพิเศษหญิง','พลเรือเอกพิเศษหญิง','พลเรือโทพิเศษหญิง','พลเรือตรีพิเศษหญิง','พลเรือจัตวาพิเศษหญิง','นาวาเอกพิเศษหญิง','นาวาโทพิเศษหญิง','นาวาตรีพิเศษหญิง','เรือเอกพิเศษหญิง','เรือโทพิเศษหญิง','เรือตรีพิเศษหญิง','พันจ่าเอกพิเศษหญิง','พันจ่าโทพิเศษหญิง','พันจ่าตรีพิเศษหญิง','จ่าเอกพิเศษหญิง','จ่าโทพิเศษหญิง','จ่าตรีพิเศษหญิง','จอมพลอากาศพิเศษหญิง','พลอากาศเอกพิเศษหญิง','พลอากาศโทพิเศษหญิง','พลอากาศตรีพิเศษหญิง','พลอากาศจัตวาพิเศษหญิง','นาวาอากาศเอกพิเศษหญิง','นาวาอากาศโทพิเศษหญิง','นาวาอากาศตรีพิเศษหญิง','เรืออากาศเอกพิเศษหญิง','เรืออากาศโทพิเศษหญิง','เรืออากาศตรีพิเศษหญิง','พันจ่าอากาศเอกพิเศษหญิง','พันจ่าอากาศโทพิเศษหญิง','พันจ่าอากาศตรีพิเศษหญิง','จ่าอากาศเอกพิเศษหญิง','จ่าอากาศโทพิเศษหญิง','จ่าอากาศตรีพิเศษหญิง','พลตำรวจเอกพิเศษหญิง','พลตำรวจโทพิเศษหญิง','พลตำรวจตรีพิเศษหญิง','พลตำรวจจัตวาพิเศษหญิง','พันตำรวจเอกพิเศษหญิง','พันตำรวจโทพิเศษหญิง','พันตำรวจตรีพิเศษหญิง','ร้อยตำรวจเอกพิเศษหญิง','ร้อยตำรวจโทพิเศษหญิง','ร้อยตำรวจตรีพิเศษหญิง','ดาบตำรวจพิเศษหญิง','จ่าสิบตำรวจพิเศษหญิง','สิบตำรวจเอกพิเศษหญิง','สิบตำรวจโทพิเศษหญิง','สิบตำรวจตรีพิเศษหญิง','จอมพลพิเศษ','พลเอกพิเศษ','พลโทพิเศษ','พลตรีพิเศษ','พลจัตวาพิเศษ','พันเอกพิเศษ','พันโทพิเศษ','พันตรีพิเศษ','ร้อยเอกพิเศษ','ร้อยโทพิเศษ','ร้อยตรีพิเศษ','จ่าสิบเอกพิเศษพิเศษ','จ่าสิบเอกพิเศษ','จ่าสิบโทพิเศษ','จ่าสิบตรีพิเศษ','สิบเอกพิเศษ','สิบโทพิเศษ','สิบตรีพิเศษ','จอมพลเรือพิเศษ','พลเรือเอกพิเศษ','พลเรือโทพิเศษ','พลเรือตรีพิเศษ','พลเรือจัตวาพิเศษ','นาวาเอกพิเศษ','นาวาโทพิเศษ','นาวาตรีพิเศษ','เรือเอกพิเศษ','เรือโทพิเศษ','เรือตรีพิเศษ','พันจ่าเอกพิเศษ','พันจ่าโทพิเศษ','พันจ่าตรีพิเศษ','จ่าเอกพิเศษ','จ่าโทพิเศษ','จ่าตรีพิเศษ','จอมพลอากาศพิเศษ','พลอากาศเอกพิเศษ','พลอากาศโทพิเศษ','พลอากาศตรีพิเศษ','พลอากาศจัตวาพิเศษ','นาวาอากาศเอกพิเศษ','นาวาอากาศโทพิเศษ','นาวาอากาศตรีพิเศษ','เรืออากาศเอกพิเศษ','เรืออากาศโทพิเศษ','เรืออากาศตรีพิเศษ','พันจ่าอากาศเอกพิเศษ','พันจ่าอากาศโทพิเศษ','พันจ่าอากาศตรีพิเศษ','จ่าอากาศเอกพิเศษ','จ่าอากาศโทพิเศษ','จ่าอากาศตรีพิเศษ','พลตำรวจเอกพิเศษ','พลตำรวจโทพิเศษ','พลตำรวจตรีพิเศษ','พลตำรวจจัตวาพิเศษ','พันตำรวจเอกพิเศษ','พันตำรวจโทพิเศษ','พันตำรวจตรีพิเศษ','ร้อยตำรวจเอกพิเศษ','ร้อยตำรวจโทพิเศษ','ร้อยตำรวจตรีพิเศษ','ดาบตำรวจพิเศษ','จ่าสิบตำรวจพิเศษ','สิบตำรวจเอกพิเศษ','สิบตำรวจโทพิเศษ','สิบตำรวจตรีพิเศษ','จอมพลหญิง','พลเอกหญิง','พลโทหญิง','พลตรีหญิง','พลจัตวาหญิง','พันเอกหญิง','พันโทหญิง','พันตรีหญิง','ร้อยเอกหญิง','ร้อยโทหญิง','ร้อยตรีหญิง','จ่าสิบเอกพิเศษหญิง','จ่าสิบเอกหญิง','จ่าสิบโทหญิง','จ่าสิบตรีหญิง','สิบเอกหญิง','สิบโทหญิง','สิบตรีหญิง','จอมพลเรือหญิง','พลเรือเอกหญิง','พลเรือโทหญิง','พลเรือตรีหญิง','พลเรือจัตวาหญิง','นาวาเอกหญิง','นาวาโทหญิง','นาวาตรีหญิง','เรือเอกหญิง','เรือโทหญิง','เรือตรีหญิง','พันจ่าเอกหญิง','พันจ่าโทหญิง','พันจ่าตรีหญิง','จ่าเอกหญิง','จ่าโทหญิง','จ่าตรีหญิง','จอมพลอากาศหญิง','พลอากาศเอกหญิง','พลอากาศโทหญิง','พลอากาศตรีหญิง','พลอากาศจัตวาหญิง','นาวาอากาศเอกหญิง','นาวาอากาศโทหญิง','นาวาอากาศตรีหญิง','เรืออากาศเอกหญิง','เรืออากาศโทหญิง','เรืออากาศตรีหญิง','พันจ่าอากาศเอกหญิง','พันจ่าอากาศโทหญิง','พันจ่าอากาศตรีหญิง','จ่าอากาศเอกหญิง','จ่าอากาศโทหญิง','จ่าอากาศตรีหญิง','พลตำรวจเอกหญิง','พลตำรวจโทหญิง','พลตำรวจตรีหญิง','พลตำรวจจัตวาหญิง','พันตำรวจเอกหญิง','พันตำรวจโทหญิง','พันตำรวจตรีหญิง','ร้อยตำรวจเอกหญิง','ร้อยตำรวจโทหญิง','ร้อยตำรวจตรีหญิง','ดาบตำรวจหญิง','จ่าสิบตำรวจหญิง','สิบตำรวจเอกหญิง','สิบตำรวจโทหญิง','สิบตำรวจตรีหญิง','จอมพล','พลเอก','พลโท','พลตรี','พลจัตวา','พันเอก','พันโท','พันตรี','ร้อยเอก','ร้อยโท','ร้อยตรี','จ่าสิบเอกพิเศษ','จ่าสิบเอก','จ่าสิบโท','จ่าสิบตรี','สิบเอก','สิบโท','สิบตรี','จอมพลเรือ','พลเรือเอก','พลเรือโท','พลเรือตรี','พลเรือจัตวา','นาวาเอก','นาวาโท','นาวาตรี','เรือเอก','เรือโท','เรือตรี','พันจ่าเอก','พันจ่าโท','พันจ่าตรี','จ่าเอก','จ่าโท','จ่าตรี','จอมพลอากาศ','พลอากาศเอก','พลอากาศโท','พลอากาศตรี','พลอากาศจัตวา','นาวาอากาศเอก','นาวาอากาศโท','นาวาอากาศตรี','เรืออากาศเอก','เรืออากาศโท','เรืออากาศตรี','พันจ่าอากาศเอก','พันจ่าอากาศโท','พันจ่าอากาศตรี','จ่าอากาศเอก','จ่าอากาศโท','จ่าอากาศตรี','พลตำรวจเอก','พลตำรวจโท','พลตำรวจตรี','พลตำรวจจัตวา','พันตำรวจเอก','พันตำรวจโท','พันตำรวจตรี','ร้อยตำรวจเอก','ร้อยตำรวจโท','ร้อยตำรวจตรี','ดาบตำรวจ','จ่าสิบตำรวจ','สิบตำรวจเอก','สิบตำรวจโท','สิบตำรวจตรี']   
    c4 = ['แพทย์หญิง','นายแพทย์','ทันตแพทย์หญิง','ทันตแพทย์','นางสาว','นาง','นาย']
    c5 = ['หม่อมหลวง','คุณหญิง','ท่านหญิง','ท่านผู้หญิง','หม่อมราชวงศ์หญิง','หม่อมราชวงศ์','หม่อมเจ้าหญิง','หม่อมเจ้า']


    for i in c:
        if a.startswith(i) == True:
            a = front(a,i)
            prefix = i
            break
    for i in c1:
        if a.startswith(i) == True:
            a = front(a,i)
            prefix = i
            break
    for i in c2:
        if a.startswith(i) == True:
            a = front(a,i)
            prefix = i
            break
    for i in c3:
        if a.startswith(i) == True:
            a = front(a,i)
            prefix = i
            break
    for i in c4:
        if a.startswith(i) == True:
            a = front(a,i)
            prefix = i
            break
    for i in c5:
        if a.startswith(i) == True:
            a = front(a,i)
            prefix = i
            break
    return a, prefix
   
def deltitleshort(str):
    a = str
    b = ''
    s  = ['พล.อ.','พล.ท.','พล.ต','พล.จ.','พ.อ.','พ.ท.','พ.ต.','ร.อ.','ร.ท.','ร.ต.','จ.ส.อ.','จ.ส.ท.','จ.ส.ต.','ส.อ.','ส.ท.','ส.ต.','พล.ร.อ.','พล.ร.ท.','พล.ร.ต.','พล.ร.จ.','น.อ.','น.ท.','น.ต.','พ.จ.อ.','พ.จ.ท.','พ.จ.ต.','จ.อ.','จ.ท.','จ.ต.','พล.อ.อ.','พล.อ.ท.','พล.อ.ต.','พล.อ.จ.','พ.อ.อ.','พ.อ.ท.','พ.อ.ต.','พล.ต.อ.','พล.ต.ท.','พล.ต.ต.','พล.ต.จ.','พ.ต.อ.','พ.ต.ท.','พ.ต.ต.','ร.ต.อ.','ร.ต.ท.','ร.ต.ต.','ด.ต.','จ.ส.ต.','ส.ต.อ.','ส.ต.ท.','ส.ต.ต.','พญ.','นพ.','ดร.','น.ส.','ม.ล.','ม.ร.ว','ม.จ.','ผศ.','รศ.','ศ.','อ.']
    s1 = ('พญ.','นพ.','ดร.','น.ส.','น.สพ.','สพ.ญ.','ภญ.','ภกญ.')
    s2 = ('ผศ.','รศ.','ศ.','อ.')
    s3 = ('ม.ล.','ม.ร.ว','ม.จ.')
    for i in range(0,a.rfind('.')+1):
        b = b+a[i]

    prefix = ''
    for i in s:
        if b.endswith(i) == True:
            a = front(a,b)
            prefix = b
            for i in s1:
                if b.endswith(i) == True:
                    return a, prefix
            for i in s2:
                if b.endswith(i) == True:
                    if a.startswith('(พิเศษ)') == True:
                        a = front(a,'(พิเศษ)')
                        prefix += '(พิเศษ)'
                        return a, prefix
                    elif a.startswith('พิเศษ') == True:
                        a = front(a,'พิเศษ')
                        prefix += 'พิเศษ'
                        return a, prefix
                    else:
                        return a, prefix
            for i in s3:
                if b.endswith(i) == True:
                    if a.startswith('หญิง') == True:
                        a = front(a,'หญิง')
                        prefix += ('หญิง')
                        return a, prefix
                    elif a.startswith('(หญิง)') == True:
                        a = front(a,'(หญิง)')
                        prefix += '(หญิง)'
                        return a, prefix
            if a.startswith('(พิเศษ)') == True:
                a = front(a,'(พิเศษ)')
                prefix += '(พิเศษ)'
            elif a.startswith('พิเศษ') == True:
                a = front(a,'พิเศษ')
                prefix += 'พิเศษ'
            if a.startswith('หญิง') == True:
                a = front(a,'หญิง')
                prefix += 'หญิง'
            elif a.startswith('(หญิง)') == True:
                a = front(a,'(หญิง)')
                prefix += '(หญิง)'
            return a, prefix
    else:
        return a, prefix

def delnumber(str):
    p = ['0','1','2','3','4','5','6','7','8','9']
    a = []
    b = ''
    j = 0
    for i in str:
        a.append(i)
    while j < len(a):
        if a[j] in p:
            del a[j]
            j = j-1
        j = j+1   
    for i in a:
        b = b + i
    return b

def celanSpace(str):
    str = " ".join(str.split())
    return str.strip()

def delengtitle(str):
    a = str
    b= ''
    # c = ('Md.','MD.','md.','Mrs.','MRS.','mrs.','Ph.D.','Associate.','Assoc.','Asso.','Asst.','Assist.','Professor.','Prof.','Dr.','Mr.','Ms.','associate.','assoc.','asso.','asst.','assist.','professor.','prof.','dr.','mr.','ms.','ASSOCIATE.','ASSOC.','ASSO.','ASST.','ASSIST.','PROFESSOR.','PROF.','DR.','MR.','MS.',
    #      'Md ','MD ','md ','Mrs ','MRS ','mrs ','Ph.D ','Associate ','Assoc ','Asso ','Asst ','Assist ','Professor ','Prof ','Dr ','Mr ','Ms ','associate ','assoc ','asso ','asst ','assist ','professor ','prof ','dr ','mr ','ms ','ASSOCIATE ','ASSOC ','ASSO ','ASST ','ASSIST ','PROFESSOR ','PROF ','DR ','MR ','MS ')
    c = ('Associate.','Assoc.','Asso.','Asst.','Assist.','associate.','assoc.','asso.','asst.','assist.','ASSOCIATE.','ASSOC.','ASSO.','ASST.','ASSIST.','Associate ','Assoc ','Asso ','Asst ','Assist ','associate ','assoc ','asso ','asst ','assist ','ASSOCIATE ','ASSOC ','ASSO ','ASST ','ASSIST ',
          'Ph.D.','Professor.','Prof.','professor.','prof.','dr.','PROFESSOR.','PROF.','Ph.D ','Professor ','Prof ','professor ','prof ','PROFESSOR ','PROF ',
          'Dr.','DR.','Dr ','dr ','DR ',
          'Md.','MD.','md.','Md ','MD ','md ',
          'Mrs.','MRS.','mrs.','Mr.','Ms.','mr.','ms.','MR.','MS.','Mrs ','MRS ','mrs ','Mr ','Ms ','mr ','ms ','MR ','MS ')
    for i in range(0,a.rfind('.')+1):
        b += a[i]

    prefix = ''
    
    found = True
    while found:
      found = False
      for i in c:
          if a.find(i) != -1:
              # a = front(a,b)
              a = a.replace(i,"")
              found = True
              prefix = prefix + i
              break
    return a, prefix

In [ ]:
def delAllPrefix(str):
  str = delnumber(str)
  str, prefix1 = deltitlefull(str)
  str, prefix2 = deltitleshort(str)
  str, prefix3 = delengtitle(str)
  str = celanSpace(str)
  prefix = prefix1+prefix2+prefix3
  return str, prefix

def cleanName(row):
  clean_name, prefix = delAllPrefix(row['new_name'])
  clean_name = clean_name.replace(',','')
  row['clean_name'] = clean_name
  row['prefix'] = prefix
  return row

In [ ]:
#ทำการจัดการคำ prefix ที่นำหน้าชื่อแล้วเอาค่าที่ถูกกำจัด มาใส่ในคอลัมน์ใหม่ที่ชื่อว่า clean_name
df_new = df_new.apply(cleanName,axis=1)

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:4681: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta={'_index': 'object', '_type': 'object', '_id': 'object', '_score': 'int64', '_source.elt': 'object', '_source.mdate': 'object', '_source.key': 'object', '_source.author': 'object', '_source.ee': 'object', '_source.title': 'object', '_source.pages': 'object', '_source.year': 'int64', '_source.volume': 'object', '_source.journal': 'object', '_source.url': 'object', '_source.file': 'object', '_source.no': 'int64', '_source.pullDate': 'object', '_source.number': 'object', '_source.i': 'object', '_source.sup': 'object', '_source.sub': 'object', '_sou

In [ ]:
# df_new.map_partitions(len).compute()

In [ ]:
# df_new.head()

In [ ]:
#ทำการตรวจสอบชื่อจากคอลัมน์ที่ชื่อว่า clean_name ว่าเป็นภาษาอะไร แล้วเอาค่าที่ได้มาใส่ในคอลัมน์ที่ขื่อว่า language ซึ่งสามารถมีค่าได้ดังนี้
# th    คือภาษาไทย
# eng   คือภาษาอังกฤษ
# other คือที่นอกเหนือภาษาไทย และ ภาษาอังกฤษ
df_new['language'] = df_new['clean_name'].apply(language)

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:3519: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('clean_name', 'object'))

  warnings.warn(meta_warning(meta))


In [ ]:
def bookname(row):
  if row['_source.elt'].strip()=='article':
    row['bookName'] = row['_source.journal']
  else:
    row['bookName'] = row['_source.booktitle']
  return row

In [ ]:
# ทำการสร้างคอลัมน์ใหม่ที่ชื่อว่า bookName 
df_new = df_new.apply(bookname,axis=1)

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:4681: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta={'_index': 'object', '_type': 'object', '_id': 'object', '_score': 'int64', '_source.elt': 'object', '_source.mdate': 'object', '_source.key': 'object', '_source.author': 'object', '_source.ee': 'object', '_source.title': 'object', '_source.pages': 'object', '_source.year': 'int64', '_source.volume': 'object', '_source.journal': 'object', '_source.url': 'object', '_source.file': 'object', '_source.no': 'int64', '_source.pullDate': 'object', '_source.number': 'object', '_source.i': 'object', '_source.sup': 'object', '_source.sub': 'object', '_sou

In [ ]:
#ทำการสร้าง Dataframe ใหม่สำหรับแบ่งตามแต่ละภาษา
df_thai = df_new[df_new['language']=='th']
df_eng = df_new[df_new['language']=='eng']
df_other = df_new[df_new['language']=='other']

In [ ]:
df_new.columns

Index(['_index', '_type', '_id', '_score', '_source.elt', '_source.mdate',
       '_source.key', '_source.author', '_source.ee', '_source.title',
       '_source.pages', '_source.year', '_source.volume', '_source.journal',
       '_source.url', '_source.file', '_source.no', '_source.pullDate',
       '_source.number', '_source.i', '_source.sup', '_source.sub',
       '_source.note', '_source.editor', '_source.isbn', '_source.booktitle',
       '_source.series', '_source.publisher', '_source.crossref',
       '_source.cite', '_source.cdrom', '_source.school', '_source.month',
       '_source.tt', '_source.address', '_source.chapter', 'new_name',
       'first_name', 'first_author', 'clean_name', 'prefix', 'language',
       'bookName'],
      dtype='object')

# create Author Table

In [ ]:
# ทำการดึงชื่อที่ไม่ซ้ำกันจากคอลัมน์ที่ชื่อว่า clean_name มาใส่ในตัวแปรประเภท Series ที่ชื่อว่า uniq_name
uniq_name = df_new['clean_name'].unique()

In [ ]:
uniq_name

Dask Series Structure:
npartitions=1
    object
       ...
Name: clean_name, dtype: object
Dask Name: unique-agg, 582 tasks

In [ ]:
# ทำการแปลงตัวแปรประเภท Series เป็น Dataframe
df_unique_name = uniq_name.to_frame()

In [ ]:
df_unique_name

Dask DataFrame Structure:
              clean_name
npartitions=1           
                  object
                     ...
Dask Name: to_frame, 583 tasks

In [ ]:
# ทำการสร้าง id ให้แต่ละชื่อโดยชื่อแรกเริ่มต้นที่ id = 606480
start_id = 606480
df_unique_name['id'] = df_unique_name.index + start_id

In [ ]:
df_unique_name

Dask DataFrame Structure:
              clean_name     id
npartitions=1                  
                  object  int64
                     ...    ...
Dask Name: assign, 586 tasks

In [ ]:
# ทำการ join dataframe df_new กับ df_unique_name เพื่อที่เราจะได้เอา id ของ author มาผูกกับ Paper

result_all = dd.merge(df_new,
                       df_unique_name,
                       left_on='clean_name',
                       right_on='clean_name',
                       how='left')

# Create Publish

## Create Publish All

In [ ]:
result_all.columns

Index(['_index', '_type', '_id', '_score', '_source.elt', '_source.mdate',
       '_source.key', '_source.author', '_source.ee', '_source.title',
       '_source.pages', '_source.year', '_source.volume', '_source.journal',
       '_source.url', '_source.file', '_source.no', '_source.pullDate',
       '_source.number', '_source.i', '_source.sup', '_source.sub',
       '_source.note', '_source.editor', '_source.isbn', '_source.booktitle',
       '_source.series', '_source.publisher', '_source.crossref',
       '_source.cite', '_source.cdrom', '_source.school', '_source.month',
       '_source.tt', '_source.address', '_source.chapter', 'new_name',
       'first_name', 'first_author', 'clean_name', 'prefix', 'language',
       'bookName', 'id'],
      dtype='object')

In [ ]:
#ทำการเปลี่ยนชื่อคอลัมน์ตามที่เรากำหนด
result_all = result_all.rename(columns={"id": "auth_ID", "first_author": "firstAuthor","_id":"source_ID","_source.no":"paper_ID","_source.title":"paperTitle","_source.elt":"paperType","_source.pages":"paperPage","_source.mdate":"publishedDate","_source.year":"publishedYear","_source.publisher":"publisherName","_source.number":"bookNo","_source.volume":"bookVolume","_source.editor":"bookEditor","_source.series":"bookSeries","_source.ee":"DOI","_source.isbn":"ISSN","_source.url":"citation","_source.file":"refURL","_source.crossref":"crossRef"})

In [ ]:
#ทำการ Drop คอลัมน์ที่ไม่ใช้ออก
result_all = result_all.drop(['_index', '_type', '_score','first_name',
       '_source.key','_source.author','_source.pullDate','_source.cite','_source.cdrom','_source.school',
       '_source.month','_source.tt','_source.address','_source.chapter','new_name',
       '_source.journal', '_source.i', '_source.sup', '_source.sub', '_source.note','_source.booktitle',
       'language','prefix'],axis=1)

In [ ]:
result_all.columns

Index(['source_ID', 'paperType', 'publishedDate', 'DOI', 'paperTitle',
       'paperPage', 'publishedYear', 'bookVolume', 'citation', 'refURL',
       'paper_ID', 'bookNo', 'bookEditor', 'ISSN', 'bookSeries',
       'publisherName', 'crossRef', 'firstAuthor', 'clean_name', 'bookName',
       'auth_ID'],
      dtype='object')

In [ ]:
# ทำการสร้าง คอลัมน์ที่ยังไม่เคยมีขึ้นมา แล้วใส่ค่า Default

# result_all['auth_ID'] = ''
# result_all["firstAuthor"] = ''
result_all['sourceName'] = 'dblp-xml'
# result_all['paperType'] = ''

# result_all['paper_ID']=''
# result_all['paperTitle']=''
result_all['paperAbtract_th'] = ''
result_all['paperAbtract_en'] = ''
result_all['paperKeywords'] = ''
# result_all['paperPage'] = ''
# result_all['publishedDate'] = ''
# result_all['publishedYear'] = ''
# result_all['publisherName'] = ''
# result_all['bookName'] = ''
# result_all['bookNo'] = ''
# result_all['bookVolume'] = ''

# result_all['bookEditor'] = ''
# result_all['bookSeries'] = ''
result_all['Fund'] = ''
# result_all['DOI'] = ''
# result_all['ISSN'] = ''
# result_all['citation'] = ''
# result_all['refURL']=''
# result_all['crossRef'] = ''

In [ ]:
#สร้างตัวแปรที่ชื่อว่า all_column เพื่อไว้สำหรับจัดลำดับของ คอลัมน์ที่ต้องการ
all_column =  ["auth_ID","firstAuthor","sourceName","source_ID","paper_ID",
               "paperTitle","paperType","paperAbtract_th","paperAbtract_en",
               "paperKeywords","paperPage","publishedDate","publishedYear",
               "publisherName","bookName","bookNo","bookVolume","bookEditor",
               "bookSeries","Fund","DOI","ISSN","citation","refURL","crossRef",
               "clean_name"]
len(all_column)

26

In [ ]:
len(result_all.columns)

26

In [ ]:
result_all = result_all[all_column]

## Check point 3

In [ ]:
def indexName(df, name):
    df.index.name = name
    return df

In [ ]:
#ทำการ reset index ใหม่
result_all = result_all.map_partitions(indexName,'id')

In [ ]:
result_all.index.name = 'id'

In [ ]:
result_all.visualize()

In [ ]:
result_all.dtypes

auth_ID             int64
firstAuthor        object
sourceName         object
source_ID          object
paper_ID            int64
paperTitle         object
paperType          object
paperAbtract_th    object
paperAbtract_en    object
paperKeywords      object
paperPage          object
publishedDate      object
publishedYear       int64
publisherName      object
bookName           object
bookNo             object
bookVolume         object
bookEditor         object
bookSeries         object
Fund               object
DOI                object
ISSN               object
citation           object
refURL             object
crossRef           object
clean_name         object
dtype: object

In [ ]:

result_all.to_csv('/content/dblp-xml/publish/dblp-xml_publish_all_*.csv')
!cp -R /content/dblp-xml/publish/* /content/drive/MyDrive/KnowledgeGraph/Integrated/dblp-xml/publish



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  del sys.path[0]
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/dist-packages/ipyk

## Check Point 4

In [ ]:
!cp /content/drive/MyDrive/KnowledgeGraph/Integrated/dblp-xml/publish/* /content/dblp-xml/publish/

In [ ]:
path_file = '/content/dblp-xml/publish/dblp-xml_publish_all_*.csv'

In [ ]:
#ทำการกำหนด ประเภทของข้อมูลแต่ละคอลัมน์ สำหรับเตรียมการอ่านข้อมูล csv
types = {'id':'int64',
  'auth_ID':'int64',
  'firstAuthor':'object',
  'sourceName':'object',
  'source_ID':'object',
  'paper_ID':'int64',
  'paperTitle':'object',
  'paperType':'object',
  'paperAbtract_th':'object',
  'paperAbtract_en':'object',
  'paperKeywords':'object',
  'paperPage':'object',
  'publishedDate':'object',
  'publishedYear':'int64',
  'publisherName':'object',
  'bookName':'object',
  'bookNo':'object',
  'bookVolume':'object',
  'bookEditor':'object',
  'bookSeries':'object',
  'Fund':'object',
  'DOI':'object',
  'ISSN':'object',
  'citation':'object',
  'refURL':'object',
  'crossRef':'object',
  'clean_name':'object' }

In [ ]:
#ทำการอ่านข้อมูลจากไฟล์ csv
result_all = dd.read_csv(path_file,dtype=types, header=0).set_index("id")

In [ ]:
result_all.dtypes

auth_ID             int64
firstAuthor        object
sourceName         object
source_ID          object
paper_ID            int64
paperTitle         object
paperType          object
paperAbtract_th    object
paperAbtract_en    object
paperKeywords      object
paperPage          object
publishedDate      object
publishedYear       int64
publisherName      object
bookName           object
bookNo             object
bookVolume         object
bookEditor         object
bookSeries         object
Fund               object
DOI                object
ISSN               object
citation           object
refURL             object
crossRef           object
clean_name         object
dtype: object

In [ ]:
# result_all.head()

In [ ]:
df_unique_name = result_all[['auth_ID','clean_name']]

In [ ]:
df_unique_name = df_unique_name.dropna()
df_unique_name = df_unique_name.drop_duplicates()

In [ ]:
#ทำการเปลี่ยนชื่อคอลัมน์ตามที่เรากำหนด
df_unique_name = df_unique_name.rename(columns={"auth_ID": "id"})

# df_author

In [ ]:
#ทำการเปลี่ยนชื่อคอลัมน์ตามที่เรากำหนด
df_unique_name = df_unique_name.rename(columns={"clean_name": "authFullName"})

In [ ]:
# ทำการตรวจสอบชื่อจากคอลัมน์ที่ชื่อว่า authFullName ว่าเป็นภาษาอะไร แล้วเอาค่าที่ได้มาใส่ในคอลัมน์ที่ขื่อว่า language ซึ่งสามารถมีค่าได้ดังนี้
# th    คือภาษาไทย
# eng   คือภาษาอังกฤษ
# other คือที่นอกเหนือภาษาไทย และ ภาษาอังกฤษ
df_unique_name['language'] = df_unique_name['authFullName'].apply(language)

/usr/local/lib/python3.7/dist-packages/dask/dataframe/core.py:3519: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('authFullName', 'object'))

  warnings.warn(meta_warning(meta))


In [ ]:
# ทำการสร้าง dataframe เพื่อเก็บข้อมูลของ author ในแต่ละภาษา

result_author_thai = df_unique_name[df_unique_name['language']=='th']

result_author_eng = df_unique_name[df_unique_name['language']=='eng']

result_author_other = df_unique_name[df_unique_name['language']=='other']

In [ ]:
result_author_thai

Dask DataFrame Structure:
                  id authFullName language
npartitions=1                             
               int64       object   object
                 ...          ...      ...
Dask Name: getitem, 679 tasks

In [ ]:
result_author_eng

Dask DataFrame Structure:
                  id authFullName language
npartitions=1                             
               int64       object   object
                 ...          ...      ...
Dask Name: getitem, 679 tasks

In [ ]:
result_author_other

Dask DataFrame Structure:
                  id authFullName language
npartitions=1                             
               int64       object   object
                 ...          ...      ...
Dask Name: getitem, 679 tasks

In [ ]:
# ทำการสร้าง dataframe เพื่อเก็บข้อมูลของ Author ในแต่ละภาษา

result_author_thai = df_unique_name[df_unique_name['language']=='th']

result_author_eng = df_unique_name[df_unique_name['language']=='eng']

result_author_other = df_unique_name[df_unique_name['language']=='other']

In [ ]:
# result_author_eng[['id','authFullName']].to_csv('/content/dblp-xml/authorEN/dblp-xml_author_eng_*.csv')
# !cp -R /content/dblp-xml/authorEN/* /content/drive/MyDrive/KnowledgeGraph/Integrated/dblp-xml/authorEN

result_author_thai[['id','authFullName']].to_csv('/content/dblp-xml/authorTH/dblp-xml_author_thai_*.csv')
!cp -R /content/dblp-xml/authorTH/* /content/drive/MyDrive/KnowledgeGraph/Integrated/dblp-xml/authorTH

result_author_other[['id','authFullName']].to_csv('/content/dblp-xml/authorOther/dblp-xml_author_other_*.csv')
!cp -R /content/dblp-xml/authorOther/* /content/drive/MyDrive/KnowledgeGraph/Integrated/dblp-xml/authorOther